# Recommendation Systems with Pytorch

This Colab notebook complements the course on [Recommendation Systems](https://developers.google.com/machine-learning/recommendation/). Specifically, we'll be using matrix factorization to learn user and movie embeddings.

**Note**: This is just the Pytorch version of the [colab](https://colab.research.google.com/github/google/eng-edu/blob/main/ml/recommendation-systems/recommendation-systems.ipynb) in tensorflow



# Introduction

We will create a movie recommendation system based on the [MovieLens](https://movielens.org/) dataset available [here](http://grouplens.org/datasets/movielens/).  The data consists of movies ratings (on a scale of 1 to 5).

## Outline
  1. Exploring the MovieLens Data (10 minutes)
  1. Preliminaries (25 minutes)
  1. Training a matrix factorization model (15 minutes)
  1. Inspecting the Embeddings (15 minutes)
  1. Regularization in matrix factorization (15 minutes)


## Setup

Let's get started by importing the required packages.

In [1]:
from __future__ import print_function

import numpy as np
import pandas as pd
import collections
from mpl_toolkits.mplot3d import Axes3D
from IPython import display
from matplotlib import pyplot as plt
import sklearn
import sklearn.manifold

In [2]:
print("Installing Altair...")
%pip install git+git://github.com/altair-viz/altair.git
import altair as alt

Installing Altair...
  Cloning git://github.com/altair-viz/altair.git to c:\users\nijuma~1\appdata\local\temp\pip-req-build-_03fl3vb
fatal: unable to look up github.com (port 9418) (No such host is known. )
Note: you may need to restart the kernel to use updated packages.


Command "git clone -q git://github.com/altair-viz/altair.git C:\Users\NIJUMA~1\AppData\Local\Temp\pip-req-build-_03fl3vb" failed with error code 128 in None


In [3]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.distributions import normal

In [4]:
def mask(df, key, function):
  """Returns a filtered dataframe, by applying function to key"""
  return df[function(df[key])]

def flatten_cols(df):
  df.columns = [' '.join(col).strip() for col in df.columns.values]
  return df

pd.DataFrame.mask = mask
pd.DataFrame.flatten_cols = flatten_cols

Get the Dataset

In [6]:
# Download MovieLens data.
print("Downloading movielens data...")
from urllib.request import urlretrieve
import zipfile

urlretrieve("http://files.grouplens.org/datasets/movielens/ml-100k.zip", "movielens.zip")
zip_ref = zipfile.ZipFile('movielens.zip', "r")
zip_ref.extractall()
print("Done. Dataset contains:")
print(zip_ref.read('ml-100k/u.info'))

# Load each data set (users, movies, and ratings).
users_cols = ['user_id', 'age', 'sex', 'occupation', 'zip_code']
users = pd.read_csv(
    'ml-100k/u.user', sep='|', names=users_cols, encoding='latin-1')

ratings_cols = ['user_id', 'movie_id', 'rating', 'unix_timestamp']
ratings = pd.read_csv(
    'ml-100k/u.data', sep='\t', names=ratings_cols, encoding='latin-1')


Done. Dataset contains:
b'943 users\n1682 items\n100000 ratings\n'


In [7]:
users.head()

user_id  age sex  occupation zip_code
0        1   24   M  technician    85711
1        2   53   F       other    94043
2        3   23   M      writer    32067
3        4   24   M  technician    43537
4        5   33   F       other    15213

In [8]:
ratings.head()

user_id  movie_id  rating  unix_timestamp
0      196       242       3       881250949
1      186       302       3       891717742
2       22       377       1       878887116
3      244        51       2       880606923
4      166       346       1       886397596

In [9]:

# The movies file contains a binary feature for each genre.
genre_cols = [
    "genre_unknown", "Action", "Adventure", "Animation", "Children", "Comedy",
    "Crime", "Documentary", "Drama", "Fantasy", "Film-Noir", "Horror",
    "Musical", "Mystery", "Romance", "Sci-Fi", "Thriller", "War", "Western"
]
movies_cols = [
    'movie_id', 'title', 'release_date', "video_release_date", "imdb_url"
] + genre_cols
movies = pd.read_csv(
    'ml-100k/u.item', sep='|', names=movies_cols, encoding='latin-1')


In [10]:
movies.tail()

movie_id                                      title release_date  \
1677      1678                          Mat' i syn (1997)  06-Feb-1998   
1678      1679                           B. Monkey (1998)  06-Feb-1998   
1679      1680                       Sliding Doors (1998)  01-Jan-1998   
1680      1681                        You So Crazy (1994)  01-Jan-1994   
1681      1682  Scream of Stone (Schrei aus Stein) (1991)  08-Mar-1996   

      video_release_date                                           imdb_url  \
1677                 NaN  http://us.imdb.com/M/title-exact?Mat%27+i+syn+...   
1678                 NaN  http://us.imdb.com/M/title-exact?B%2E+Monkey+(...   
1679                 NaN      http://us.imdb.com/Title?Sliding+Doors+(1998)   
1680                 NaN  http://us.imdb.com/M/title-exact?You%20So%20Cr...   
1681                 NaN  http://us.imdb.com/M/title-exact?Schrei%20aus%...   

      genre_unknown  Action  Adventure  Animation  Children  ...  Fantasy  \
1677              0       0          0          0         0  ...        0   
1678              0       0          0          0         0  ...        0   
1679              0       0          0          0         0  ...        0   
1680              0       0          0          0         0  ...        0   
1681              0       0          0          0         0  ...        0   

      Film-Noir  Horror  Musical  Mystery  Romance  Sci-Fi  Thriller  War  \
1677          0       0        0        0        0       0         0    0   
1678          0       0        0        0        1       0         1    0   
1679          0       0        0        0        1       0         0    0   
1680          0       0        0        0        0       0         0    0   
1681          0       0        0        0        0       0         0    0   

      Western  
1677        0  
1678        0  
1679        0  
1680        0  
1681        0  

[5 rows x 24 columns]

In [56]:
users.dtypes

user_id       object
age            int64
sex           object
occupation    object
zip_code      object
dtype: object

In [11]:
# Since the ids start at 1, we shift them to start at 0.
users["user_id"] = users["user_id"].apply(lambda x: str(x-1))
movies["movie_id"] = movies["movie_id"].apply(lambda x: str(x-1))
movies["year"] = movies['release_date'].apply(lambda x: str(x).split('-')[-1])
ratings["movie_id"] = ratings["movie_id"].apply(lambda x: str(x-1))
ratings["user_id"] = ratings["user_id"].apply(lambda x: str(x-1))
ratings["rating"] = ratings["rating"].apply(lambda x: float(x))

In [12]:
# Compute the number of movies to which a genre is assigned.
genre_occurences = movies[genre_cols].sum().to_dict()
genre_occurences

{'genre_unknown': 2,
 'Action': 251,
 'Adventure': 135,
 'Animation': 42,
 'Children': 122,
 'Comedy': 505,
 'Crime': 109,
 'Documentary': 50,
 'Drama': 725,
 'Fantasy': 22,
 'Film-Noir': 24,
 'Horror': 92,
 'Musical': 56,
 'Mystery': 61,
 'Romance': 247,
 'Sci-Fi': 101,
 'Thriller': 251,
 'War': 71,
 'Western': 27}

In [13]:
# Since some movies can belong to more than one genre, we create different
# 'genre' columns as follows:
# - all_genres: all the active genres of the movie.
# - genre: randomly sampled from the active genres.
def mark_genres(movies, genres):
  def get_random_genre(gs):
    active = [genre for genre, g in zip(genres, gs) if g==1]
    if len(active) == 0: 
      return 'Other'
    return np.random.choice(active)
  def get_all_genres(gs):
    active = [genre for genre, g in zip(genres, gs) if g==1]
    if len(active) == 0:
      return 'Other'
    return '-'.join(active)
  movies['genre'] = [
      get_random_genre(gs) for gs in zip(*[movies[genre] for genre in genres])]
  movies['all_genres'] = [
      get_all_genres(gs) for gs in zip(*[movies[genre] for genre in genres])]

mark_genres(movies, genre_cols)

In [14]:
# Create one merged DataFrame containing all the movielens data.
movielens = ratings.merge(movies, on='movie_id').merge(users, on='user_id')
movielens.head()

user_id movie_id  rating  unix_timestamp  \
0     195      241     3.0       881250949   
1     195      256     2.0       881251577   
2     195      110     4.0       881251793   
3     195       24     4.0       881251955   
4     195      381     4.0       881251843   

                                               title release_date  \
0                                       Kolya (1996)  24-Jan-1997   
1                                Men in Black (1997)  04-Jul-1997   
2                Truth About Cats & Dogs, The (1996)  26-Apr-1996   
3                               Birdcage, The (1996)  08-Mar-1996   
4  Adventures of Priscilla, Queen of the Desert, ...  01-Jan-1994   

   video_release_date                                           imdb_url  \
0                 NaN    http://us.imdb.com/M/title-exact?Kolya%20(1996)   
1                 NaN  http://us.imdb.com/M/title-exact?Men+in+Black+...   
2                 NaN  http://us.imdb.com/M/title-exact?Truth%20About...   
3                 NaN  http://us.imdb.com/M/title-exact?Birdcage,%20T...   
4                 NaN  http://us.imdb.com/M/title-exact?Adventures%20...   

   genre_unknown  Action  ...  Thriller  War  Western  year    genre  \
0              0       0  ...         0    0        0  1997   Comedy   
1              0       1  ...         0    0        0  1997   Action   
2              0       0  ...         0    0        0  1996  Romance   
3              0       0  ...         0    0        0  1996   Comedy   
4              0       0  ...         0    0        0  1994   Comedy   

                       all_genres  age  sex  occupation  zip_code  
0                          Comedy   49    M      writer     55105  
1  Action-Adventure-Comedy-Sci-Fi   49    M      writer     55105  
2                  Comedy-Romance   49    M      writer     55105  
3                          Comedy   49    M      writer     55105  
4                    Comedy-Drama   49    M      writer     55105  

[5 rows x 34 columns]

In [15]:
genre_cols

['genre_unknown',
 'Action',
 'Adventure',
 'Animation',
 'Children',
 'Comedy',
 'Crime',
 'Documentary',
 'Drama',
 'Fantasy',
 'Film-Noir',
 'Horror',
 'Musical',
 'Mystery',
 'Romance',
 'Sci-Fi',
 'Thriller',
 'War',
 'Western']

What is being done in the zip command

In [16]:
x = zip(*[movies[genre] for genre in genre_cols])
list(x)[:5]

[(0, 0, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0),
 (0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0),
 (0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0),
 (0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0),
 (0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0)]

In [17]:
# Utility to split the data into training and test sets.
def split_dataframe(df, holdout_fraction=0.1):
  """Splits a DataFrame into training and test sets.
  Args:
    df: a dataframe.
    holdout_fraction: fraction of dataframe rows to use in the test set.
  Returns:
    train: dataframe for training
    test: dataframe for testing
  """
  test = df.sample(frac=holdout_fraction, replace=False)
  train = df[~df.index.isin(test.index)]
  return train, test

# I. Exploring the Movielens Data
Before we dive into model building, let's inspect our MovieLens dataset. It is usually helpful to understand the statistics of the dataset.

In [18]:
users.describe()

age
count  943.000000
mean    34.051962
std     12.192740
min      7.000000
25%     25.000000
50%     31.000000
75%     43.000000
max     73.000000

In [19]:
users.describe(include=[np.object])

user_id  sex occupation zip_code
count      943  943        943      943
unique     943    2         21      795
top        126    M    student    55414
freq         1  670        196        9

In [20]:
users_ratings = (
    ratings
    .groupby('user_id', as_index=False)
    .agg({'rating': ['count', 'mean']})
    .flatten_cols()
    .merge(users, on='user_id')
)

In [21]:
users_ratings.head()

user_id  rating count  rating mean  age sex  occupation zip_code
0       0           272     3.610294   24   M  technician    85711
1       1            62     3.709677   53   F       other    94043
2      10           181     3.464088   39   F       other    30329
3     100            67     2.895522   15   M     student    05146
4     101           216     2.615741   38   M  programmer    30220

In [22]:
# The following functions are used to generate interactive Altair charts.
# We will display histograms of the data, sliced by a given attribute.

# Create filters to be used to slice the data.
occupation_filter = alt.selection_multi(fields=["occupation"])
occupation_chart = alt.Chart().mark_bar().encode(
    x="count()",
    y=alt.Y("occupation:N"),
    color=alt.condition(
        occupation_filter,
        alt.Color("occupation:N", scale=alt.Scale(scheme='category20')),
        alt.value("lightgray")),
).properties(width=300, height=300, selection=occupation_filter)

# A function that generates a histogram of filtered data.
def filtered_hist(field, label, filter):
  """Creates a layered chart of histograms.
  The first layer (light gray) contains the histogram of the full data, and the
  second contains the histogram of the filtered data.
  Args:
    field: the field for which to generate the histogram.
    label: String label of the histogram.
    filter: an alt.Selection object to be used to filter the data.
  """
  base = alt.Chart().mark_bar().encode(
      x=alt.X(field, bin=alt.Bin(maxbins=10), title=label),
      y="count()",
  ).properties(
      width=300,
  )
  return alt.layer(
      base.transform_filter(filter),
      base.encode(color=alt.value('lightgray'), opacity=alt.value(.7)),
  ).resolve_scale(y='independent')

In [23]:
# Create a chart for the count, and one for the mean.
alt.hconcat(
    filtered_hist('rating count', '# ratings / user', occupation_filter),
    filtered_hist('rating mean', 'mean user rating', occupation_filter),
    occupation_chart,
    data=users_ratings)

alt.HConcatChart(...)

### Movies

It is also useful to look at information about the movies and their ratings.

In [24]:
genre_filter = alt.selection_multi(fields=['genre'])
genre_chart = alt.Chart().mark_bar().encode(
    x="count()",
    y=alt.Y('genre'),
    color=alt.condition(
        genre_filter,
        alt.Color("genre:N"),
        alt.value('lightgray'))
).properties(height=300, selection=genre_filter)

In [25]:
movies_ratings = movies.merge(
    ratings
    .groupby('movie_id', as_index=False)
    .agg({'rating': ['count', 'mean']})
    .flatten_cols(),
    on='movie_id')

In [26]:
(movies_ratings[['title', 'rating count', 'rating mean']]
 .sort_values('rating count', ascending=False)
 .head(10))

title  rating count  rating mean
49                Star Wars (1977)           583     4.358491
257                 Contact (1997)           509     3.803536
99                    Fargo (1996)           508     4.155512
180      Return of the Jedi (1983)           507     4.007890
293               Liar Liar (1997)           485     3.156701
285    English Patient, The (1996)           481     3.656965
287                  Scream (1996)           478     3.441423
0                 Toy Story (1995)           452     3.878319
299           Air Force One (1997)           431     3.631090
120  Independence Day (ID4) (1996)           429     3.438228

In [27]:
(movies_ratings[['title', 'rating count', 'rating mean']]
 .mask('rating count', lambda x: x > 20)
 .sort_values('rating mean', ascending=False)
 .head(10))

title  rating count  \
407                              Close Shave, A (1995)           112   
317                            Schindler's List (1993)           298   
168                         Wrong Trousers, The (1993)           118   
482                                  Casablanca (1942)           243   
113  Wallace & Gromit: The Best of Aardman Animatio...            67   
63                    Shawshank Redemption, The (1994)           283   
602                                 Rear Window (1954)           209   
11                          Usual Suspects, The (1995)           267   
49                                    Star Wars (1977)           583   
177                                12 Angry Men (1957)           125   

     rating mean  
407     4.491071  
317     4.466443  
168     4.466102  
482     4.456790  
113     4.447761  
63      4.445230  
602     4.387560  
11      4.385768  
49      4.358491  
177     4.344000

In [28]:
# Display the number of ratings and average rating per movie.
alt.hconcat(
    filtered_hist('rating count', '# ratings / movie', genre_filter),
    filtered_hist('rating mean', 'mean movie rating', genre_filter),
    genre_chart,
    data=movies_ratings)

alt.HConcatChart(...)

# II. Preliminaries

Our goal is to factorize the ratings matrix $A$ into the product of a user 

embedding matrix $U$ and movie embedding matrix $V$,

 such that $A \approx UV^\top$ with
 
$U = \begin{bmatrix} u_{1} \\ \hline \vdots \\ \hline u_{N} \end{bmatrix}$ and
$V = \begin{bmatrix} v_{1} \\ \hline \vdots \\ \hline v_{M} \end{bmatrix}$.

Here
- $N$ is the number of users,
- $M$ is the number of movies,
- $A_{ij}$ is the rating of the $j$th movies by the $i$th user,
- each row $U_i$ is a $d$-dimensional vector (embedding) representing user $i$,
- each row $V_j$ is a $d$-dimensional vector (embedding) representing movie $j$,
- the prediction of the model for the $(i, j)$ pair is the dot product $\langle U_i, V_j \rangle$.



## Sparse Representation of the Rating Matrix

The rating matrix could be very large and, in general, most of the entries are unobserved, since a given user will only rate a small subset of movies. For effcient representation, we will use a [torch.sparse_coo_tensor](https://pytorch.org/docs/stable/generated/torch.sparse_coo_tensor.html). A `SparseTensor` uses three tensors to represent the matrix: `torch.sparse_coo_tensor(indices, values, size)` represents a tensor, where a value $A_{ij} = a$ is encoded by setting `indices[k] = [i, j]` and `values[k] = a`. The last tensor `size` is used to specify the shape of the full underlying matrix.

#### Toy example
Assume we have $2$ users and $4$ movies. Our toy ratings dataframe has three ratings,

user\_id | movie\_id | rating
--:|--:|--:
0 | 0 | 5.0
0 | 1 | 3.0
1 | 3 | 1.0

The corresponding rating matrix is

$$
A =
\begin{bmatrix}
5.0 & 3.0 & 0 & 0 \\
0   &   0 & 0 & 1.0
\end{bmatrix}
$$

And the SparseTensor representation is,
```python
SparseTensor(
  indices=[[0, 0], [0, 1], [1,3]],
  values=[5.0, 3.0, 1.0],
  dense_shape=[2, 4])
```

In [29]:
def build_rating_sparse_tensor(ratings_df):
  """
  Args:
    ratings_df: a pd.DataFrame with `user_id`, `movie_id` and `rating` columns.
  Returns:
    a torch.SparseTensor representing the ratings matrix.
  """
  indices = ratings_df[['user_id', 'movie_id']].values.astype(np.float32)
  values = ratings_df['rating'].values
  s = torch.sparse_coo_tensor(
      indices=indices.T,
      values=values,
      size = (users.shape[0],movies.shape[0]))
  return s

## Calculating the error

The model approximates the ratings matrix $A$ by a low-rank product $UV^\top$. We need a way to measure the approximation error. We'll start by using the Mean Squared Error of observed entries only (we will revisit this later). It is defined as

$$
\begin{align*}
\text{MSE}(A, UV^\top)
&= \frac{1}{|\Omega|}\sum_{(i, j) \in\Omega}{( A_{ij} - (UV^\top)_{ij})^2} \\
&= \frac{1}{|\Omega|}\sum_{(i, j) \in\Omega}{( A_{ij} - \langle U_i, V_j\rangle)^2}
\end{align*}
$$
where $\Omega$ is the set of observed ratings, and $|\Omega|$ is the cardinality of $\Omega$.

In [30]:
# This Function is not used as it is,however, it sused in the model class

def sparse_mean_square_error(sparse_ratings, user_embeddings, movie_embeddings):
  """
  Args:
    sparse_ratings: A SparseTensor rating matrix, of dense_shape [N, M]
    user_embeddings: A dense Tensor U of shape [N, k] where k is the embedding
      dimension, such that U_i is the embedding of user i.
    movie_embeddings: A dense Tensor V of shape [M, k] where k is the embedding
      dimension, such that V_j is the embedding of movie j.
  Returns:
    A scalar Tensor representing the MSE between the true ratings and the
      model's predictions.
  """
  
  predictions = (torch.index_select(user_embeddings,0, sparse_ratings._indices()[0,:]) \
                 *torch.index_select(movie_embeddings,0, sparse_ratings._indices()[1, :])).sum(dim=1)
  loss = torch.mse(sparse_ratings.coalesce().values(), predictions.type(torch.DoubleTensor))
  return loss

Training a Matrix Factorization model

## CFModel (Collaborative Filtering Model) helper class
This is a simple class to train a matrix factorization model using stochastic gradient descent.

The class constructor takes
- the user embeddings U (a `torch tensor`).
- the movie embeddings V, (a `torch tensor`).
- an optional list of metrics dictionaries, each mapping a string (the name of the metric) to a tensor. These are evaluated and plotted during training (e.g. training error and test error).

After training, one can access the trained embeddings using the `model.embeddings` dictionary.

Example usage:
```
U_var = ...
V_var = ...
loss = ...
model = CFModel(U_var, V_var, loss)
model.train(iterations=100, learning_rate=1.0)
user_embeddings = model.embeddings['user_id']
movie_embeddings = model.embeddings['movie_id']
```


### Exercise 4: Build a Matrix Factorization model and train it


In [31]:

class CFModel(torch.nn.Module):
  """Simple class that represents a collaborative filtering model"""
  def __init__(self, n_users,n_movies,init_stddev,embedding_dim):
    """Initializes a CFModel.
    Args:
      embedding_vars: A dictionary of tf.Variables.
      loss: A float Tensor. The loss to optimize.
      metrics: optional list of dictionaries of Tensors. The metrics in each
        dictionary will be plotted in a separate figure during training.
    """
    super().__init__()
    self.random_normal_dist = normal.Normal(0,init_stddev)
    self.U = torch.nn.Parameter(self.random_normal_dist.sample([n_users, embedding_dim])) #user_embeddings
    self.V = torch.nn.Parameter(self.random_normal_dist.sample([n_movies, embedding_dim])) #movie_embeddings
    self._metrics = {
      'train_error': 0,
      'test_error': 0
    }

  @property
  def embeddings(self):
    """The embeddings dictionary."""
    return {
      "user_id": self.U.detach().numpy(),
      "movie_id": self.V.detach().numpy()
    }

  def forward(self,sparse_ratings):
    """
      Args:
        sparse_ratings: A SparseTensor rating matrix, of dense_shape [N, M]
        self.U ->user_embeddings: A dense Tensor U of shape [N, k] where k is the embedding
          dimension, such that U_i is the embedding of user i.
        self.V ->movie_embeddings: A dense Tensor V of shape [M, k] where k is the embedding
          dimension, such that V_j is the embedding of movie j.
      Returns:
        Predictions - Product between U and V ( U dot V_transpose)
    """
    return  (torch.index_select(self.U,0, sparse_ratings._indices()[0,:]) \
                 *torch.index_select(self.V,0, sparse_ratings._indices()[1, :])).sum(dim=1)
    

In [32]:
train_ratings, test_ratings = split_dataframe(ratings)
# SparseTensor representation of the train and test datasets.
#print(f'train_shape:{train_ratings.shape}')
A_train = build_rating_sparse_tensor(train_ratings)
A_test = build_rating_sparse_tensor(test_ratings)
n_users = A_train.size()[0]
n_movies = A_train.size()[1]
#print(f'n_users:{n_users},n_movies:{n_movies}')
#print(f'A_train:{A_train}')
#print(f'A_train_Values_shape:{A_train.coalesce().values().shape}')
model = CFModel(n_users ,n_movies,init_stddev =0.5,embedding_dim=30)
loss_fn = torch.nn.MSELoss() 
optimizer = optim.SGD(model.parameters(),
                            lr=10.)

def train(model ,num_iterations,A_train):
  """
  Args:
    ratings: a DataFrame of the ratings
    embedding_dim: the dimension of the embedding vectors.
    init_stddev: float, the standard deviation of the random initial embeddings.
  Returns:
    model: a CFModel.
  """
  # Split the ratings DataFrame into train and test.
  for i in range(num_iterations+1):
    predictions = model.forward(A_train)
    #print(f'predictions_shape:{predictions.shape}')
    train_loss = loss_fn(A_train.coalesce().values(), predictions.type(torch.DoubleTensor))

    
    with torch.no_grad():
      test_predictions = model.forward(A_test)
      test_loss = loss_fn(A_test.coalesce().values(), test_predictions.type(torch.DoubleTensor))
    
      
    optimizer.zero_grad()
    train_loss.backward()
    optimizer.step()
    if (i % 10 == 0) or i == num_iterations:
          print(f'\r iteration {i}:train_error = {train_loss} ; test_error = {test_loss}',end='')


In [33]:
train(model,1000,A_train)

 iteration 1000:train_error = 0.6113150408454826 ; test_error = 2.2437753955972006

# IV. Inspecting the Embeddings

In this section, we take a closer look at the learned embeddings, by
- computing your recommendations
- looking at the nearest neighbors of some movies,
- looking at the norms of the movie embeddings,
- visualizing the embedding in a projected embedding space.

## Write a function that computes the scores of the candidates
We start by writing a function that, given a query embedding $u \in \mathbb R^d$ and item embeddings $V \in \mathbb R^{N \times d}$, computes the item scores.

As discussed in the lecture, there are different similarity measures we can use, and these can yield different results. We will compare the following:
- dot product: the score of item j is $\langle u, V_j \rangle$.
- cosine: the score of item j is $\frac{\langle u, V_j \rangle}{\|u\|\|V_j\|}$.



In [34]:
DOT = 'dot'
COSINE = 'cosine'
def compute_scores(query_embedding, item_embeddings, measure=DOT):
  """Computes the scores of the candidates given a query.
  Args:
    query_embedding: a vector of shape [k], representing the query embedding.
    item_embeddings: a matrix of shape [N, k], such that row i is the embedding
      of item i.
    measure: a string specifying the similarity measure to be used. Can be
      either DOT or COSINE.
  Returns:
    scores: a vector of shape [N], such that scores[i] is the score of item i.
  """
  u = query_embedding
  V = item_embeddings
  if measure == COSINE:
    V = V / np.linalg.norm(V, axis=1, keepdims=True)
    u = u / np.linalg.norm(u)
  scores = u.dot(V.T)
  return scores

In [35]:
def movie_neighbors(model, title_substring, measure=DOT, k=6):
  
  # Search for movie ids that match the given substring.
  ids =  movies[movies['title'].str.contains(title_substring)].index.values
  titles = movies.iloc[ids]['title'].values
  if len(titles) == 0:
    raise ValueError("Found no movies with title %s" % title_substring)
  print("Nearest neighbors of : %s." % titles[0])
  if len(titles) > 1:
    print("[Found more than one matching movie. Other candidates: {}]".format(
        ", ".join(titles[1:])))
  movie_id = ids[0]
  scores = compute_scores(
      model.embeddings["movie_id"][movie_id], model.embeddings["movie_id"],
      measure)
  score_key = measure + ' score'
  df = pd.DataFrame({
      score_key: list(scores),
      'titles': movies['title'],
      'genres': movies['all_genres']
  })
  display.display(df.sort_values([score_key], ascending=False).head(k))

### Movie Nearest neighbors

Let's look at the neareast neighbors for some of the movies.

In [36]:

movie_neighbors(model, "Aladdin", DOT)

Nearest neighbors of : Aladdin (1992).
[Found more than one matching movie. Other candidates: Aladdin and the King of Thieves (1996)]


dot score                          titles  \
94     5.345872                  Aladdin (1992)   
1017   5.154301  Tie Me Up! Tie Me Down! (1990)   
501    4.882740                  Bananas (1971)   
1512   4.819868                   Sprung (1997)   
33     4.722732     Doom Generation, The (1995)   
816    4.720414                    Frisk (1995)   

                                 genres  
94    Animation-Children-Comedy-Musical  
1017                              Drama  
501                          Comedy-War  
1512                             Comedy  
33                         Comedy-Drama  
816                               Drama

In [37]:
movie_neighbors(model, "Aladdin", COSINE)

Nearest neighbors of : Aladdin (1992).
[Found more than one matching movie. Other candidates: Aladdin and the King of Thieves (1996)]


cosine score                               titles  \
94       1.000000                       Aladdin (1992)   
247      0.744695           Grosse Pointe Blank (1997)   
173      0.744581       Raiders of the Lost Ark (1981)   
9        0.730897                   Richard III (1995)   
250      0.728537               Shall We Dance? (1996)   
110      0.726262  Truth About Cats & Dogs, The (1996)   

                                genres  
94   Animation-Children-Comedy-Musical  
247                       Comedy-Crime  
173                   Action-Adventure  
9                            Drama-War  
250                             Comedy  
110                     Comedy-Romance

It seems that the quality of learned embeddings may not be very good. This will be addressed in Section V by adding several regularization techniques. First, we will further inspect the embeddings.

## Movie Embedding Norm

We can also observe that the recommendations with dot-product and cosine are different: with dot-product, the model tends to recommend popular movies. This can be explained by the fact that in matrix factorization models, the norm of the embedding is often correlated with popularity (popular movies have a larger norm), which makes it more likely to recommend more popular items. We can confirm this hypothesis by sorting the movies by their embedding norm, as done in the next cell.

In [38]:
# @title Embedding Visualization code (run this cell)

def movie_embedding_norm(models):
  """Visualizes the norm and number of ratings of the movie embeddings.
  Args:
    model: A MFModel object.
  """
  if not isinstance(models, list):
    models = [models]
  df = pd.DataFrame({
      'title': movies['title'],
      'genre': movies['genre'],
      'num_ratings': movies_ratings['rating count'],
  })
  charts = []
  brush = alt.selection_interval()
  for i, model in enumerate(models):
    norm_key = 'norm'+str(i)
    df[norm_key] = np.linalg.norm(model.embeddings["movie_id"], axis=1)
    nearest = alt.selection(
        type='single', encodings=['x', 'y'], on='mouseover', nearest=True,
        empty='none')
    base = alt.Chart().mark_circle().encode(
        x='num_ratings',
        y=norm_key,
        color=alt.condition(brush, alt.value('#4c78a8'), alt.value('lightgray'))
    ).properties(
        selection=nearest).add_selection(brush)
    text = alt.Chart().mark_text(align='center', dx=5, dy=-5).encode(
        x='num_ratings', y=norm_key,
        text=alt.condition(nearest, 'title', alt.value('')))
    charts.append(alt.layer(base, text))
  return alt.hconcat(*charts, data=df)

def visualize_movie_embeddings(data, x, y):
  nearest = alt.selection(
      type='single', encodings=['x', 'y'], on='mouseover', nearest=True,
      empty='none')
  base = alt.Chart().mark_circle().encode(
      x=x,
      y=y,
      color=alt.condition(genre_filter, "genre", alt.value("whitesmoke")),
  ).properties(
      width=600,
      height=600,
      selection=nearest)
  text = alt.Chart().mark_text(align='left', dx=5, dy=-5).encode(
      x=x,
      y=y,
      text=alt.condition(nearest, 'title', alt.value('')))
  return alt.hconcat(alt.layer(base, text), genre_chart, data=data)

def tsne_movie_embeddings(model):
  """Visualizes the movie embeddings, projected using t-SNE with Cosine measure.
  Args:
    model: A MFModel object.
  """
  tsne = sklearn.manifold.TSNE(
      n_components=2, perplexity=40, metric='cosine', early_exaggeration=10.0,
      init='pca', verbose=True, n_iter=400)

  print('Running t-SNE...')
  V_proj = tsne.fit_transform(model.embeddings["movie_id"])
  movies.loc[:,'x'] = V_proj[:, 0]
  movies.loc[:,'y'] = V_proj[:, 1]
  return visualize_movie_embeddings(movies, 'x', 'y')

In [39]:
movie_embedding_norm(model)

alt.HConcatChart(...)

Note: Depending on how the model is initialized, you may observe that some niche movies (ones with few ratings) have a high norm, leading to spurious recommendations. This can happen if the embedding of that movie happens to be initialized with a high norm. Then, because the movie has few ratings, it is infrequently updated, and can keep its high norm. This will be alleviated by using regularization.

Try changing the value of the hyper-parameter `init_stddev`. One quantity that can be helpful is that the expected norm of a $d$-dimensional vector with entries $\sim \mathcal N(0, \sigma^2)$ is approximatley $\sigma \sqrt d$.

How does this affect the embedding norm distribution, and the ranking of the top-norm movies?

In [40]:
model_lowinit = CFModel(n_users ,n_movies,init_stddev =0.05,embedding_dim=30)
train(model_lowinit,1000,A_train)
movie_neighbors(model_lowinit, "Aladdin", DOT)
movie_neighbors(model_lowinit, "Aladdin", COSINE)
movie_embedding_norm([model, model_lowinit])

 iteration 1000:train_error = 13.732506324443342 ; test_error = 13.678219483364696Nearest neighbors of : Aladdin (1992).
[Found more than one matching movie. Other candidates: Aladdin and the King of Thieves (1996)]


dot score                                 titles  \
94     0.081597                         Aladdin (1992)   
1465   0.042061               Margaret's Museum (1995)   
292    0.040933                   Donnie Brasco (1997)   
336    0.036524               House of Yes, The (1997)   
1328   0.036517                   Low Life, The (1994)   
370    0.034955  Bridges of Madison County, The (1995)   

                                 genres  
94    Animation-Children-Comedy-Musical  
1465                              Drama  
292                         Crime-Drama  
336               Comedy-Drama-Thriller  
1328                              Drama  
370                       Drama-Romance

Nearest neighbors of : Aladdin (1992).
[Found more than one matching movie. Other candidates: Aladdin and the King of Thieves (1996)]


cosine score                    titles  \
94        1.000000            Aladdin (1992)   
429       0.492886          Duck Soup (1933)   
1370      0.489620       Machine, The (1994)   
654       0.472493        Stand by Me (1986)   
1465      0.459590  Margaret's Museum (1995)   
1552      0.459072    Underneath, The (1995)   

                                 genres  
94    Animation-Children-Comedy-Musical  
429                          Comedy-War  
1370                      Comedy-Horror  
654              Adventure-Comedy-Drama  
1465                              Drama  
1552                   Mystery-Thriller

alt.HConcatChart(...)

### Embedding visualization

Since it is hard to visualize embeddings in a higher-dimensional space (when the embedding dimension $k > 3$), one approach is to project the embeddings to a lower dimensional space. T-SNE (T-distributed Stochastic Neighbor Embedding) is an algorithm that projects the embeddings while attempting to preserve their pariwise distances. It can be useful for visualization, but one should use it with care. For more information on using t-SNE, see [How to Use t-SNE Effectively](https://distill.pub/2016/misread-tsne/).

In [41]:
tsne_movie_embeddings(model_lowinit)

Running t-SNE...
[t-SNE] Computing 121 nearest neighbors...
[t-SNE] Indexed 1682 samples in 0.000s...
[t-SNE] Computed neighbors for 1682 samples in 0.053s...
[t-SNE] Computed conditional probabilities for sample 1000 / 1682
[t-SNE] Computed conditional probabilities for sample 1682 / 1682
[t-SNE] Mean sigma: 0.238504
[t-SNE] KL divergence after 100 iterations with early exaggeration: 60.152130
[t-SNE] KL divergence after 400 iterations: 2.945693


alt.HConcatChart(...)

You can highlight the embeddings of a given genre by clicking on the genres panel (SHIFT+click to select multiple genres).

We can observe that the embeddings do not seem to have any notable structure, and the embeddings of a given genre are located all over the embedding space. This confirms the poor quality of the learned embeddings. One of the main reasons, which we will address in the next section, is that we only trained the model on observed pairs, and without regularization.

# V. Regularization In Matrix Factorization

In the previous section, our loss was defined as the mean squared error on the observed part of the rating matrix.  As discussed in the lecture, this can be problematic as the model does not learn how to place the embeddings of irrelevant movies. This phenomenon is known as *folding*.

We will add regularization terms that will address this issue. We will use two types of regularization:
- Regularization of the model parameters. This is a common $\ell_2$ regularization term on the embedding matrices, given by $r(U, V) =  \frac{1}{N} \sum_i \|U_i\|^2 + \frac{1}{M}\sum_j \|V_j\|^2$.
- A global prior that pushes the prediction of any pair towards zero, called the *gravity* term. This is given by $g(U, V) = \frac{1}{MN} \sum_{i = 1}^N \sum_{j = 1}^M \langle U_i, V_j \rangle^2$.

The total loss is then given by
$$
\frac{1}{|\Omega|}\sum_{(i, j) \in \Omega} (A_{ij} - \langle U_i, V_j\rangle)^2 + \lambda _r r(U, V) + \lambda_g g(U, V)
$$
where $\lambda_r$ and $\lambda_g$ are two regularization coefficients (hyper-parameters).

In [42]:
# Gravity Term
def gravity(U, V):
  """Creates a gravity loss given two embedding matrices."""
  return 1. / (U.shape[0]*V.shape[0]) * (
      torch.mm(U.T, U) * torch.mm(V.T, V)).sum()

In [44]:
class Regularized_CFModel(torch.nn.Module):
  """Simple class that represents a collaborative filtering model"""
  def __init__(self,init_stddev,regularization_coeff=.1, gravity_coeff=1.,embedding_dim=3):
    """Initializes a Regularized CFModel.
    Args:
      embedding_vars: A dictionary of tf.Variables.
      init_stddev: float, the standard deviation of the random initial embeddings
    """
    super().__init__()
    self.random_normal_dist = normal.Normal(0,init_stddev)
    self.regularization_coeff= regularization_coeff
    self.gravity_coeff = gravity_coeff
    self.embedding_dim = embedding_dim
    self._metrics = {
      'train_error': 0,
      'test_error': 0
    }

  @property
  def embeddings(self):
    """The embeddings dictionary."""
    return {
      "user_id": self.U.detach().numpy(),
      "movie_id": self.V.detach().numpy()
    }

  def forward(self,sparse_ratings):
    """
      Args:
        sparse_ratings: A SparseTensor rating matrix, of dense_shape [N, M]
        self.U ->user_embeddings: A dense Tensor U of shape [N, k] where k is the embedding
          dimension, such that U_i is the embedding of user i.
        self.V ->movie_embeddings: A dense Tensor V of shape [M, k] where k is the embedding
          dimension, such that V_j is the embedding of movie j.
      Returns:
        Predictions - Product between U and V ( U dot V_transpose)
    """
    return  (torch.index_select(self.U,0, sparse_ratings._indices()[0,:]) \
                 *torch.index_select(self.V,0, sparse_ratings._indices()[1, :])).sum(dim=1)


  def train(self,num_iterations ,learning_rate,ratings):
    """
    Args:
      ratings: a DataFrame of the ratings
      embedding_dim: the dimension of the embedding vectors.
      init_stddev: float, the standard deviation of the random initial embeddings.
    Returns:
      model: a CFModel.
    """
    
    # Split the ratings DataFrame into train and test.
    train_ratings, test_ratings = split_dataframe(ratings)
    # SparseTensor representation of the train and test datasets.
    A_train = build_rating_sparse_tensor(train_ratings)
    A_test = build_rating_sparse_tensor(test_ratings)

    self.U = torch.nn.Parameter(self.random_normal_dist.sample([A_train.size()[0], self.embedding_dim])) #user_embeddings
    self.V = torch.nn.Parameter(self.random_normal_dist.sample([A_train.size()[1], self.embedding_dim])) #movie_embeddings

    loss_fn = torch.nn.MSELoss() 
    optimizer = optim.SGD(self.parameters(),
                              lr=learning_rate)
  
    for i in range(num_iterations+1):
      predictions = self.forward(A_train)
      #print(f'predictions_shape:{predictions.shape}')
      error_train = loss_fn(A_train.coalesce().values(), predictions.type(torch.DoubleTensor))
      gravity_loss = self.gravity_coeff * gravity(self.U, self.V)
      
      with torch.no_grad():
        test_predictions = self.forward(A_test)
        error_test = loss_fn(A_test.coalesce().values(), test_predictions.type(torch.DoubleTensor))
      
      regularization_loss = self.regularization_coeff * (
        torch.sum(self.U*self.U)/self.U.shape[0]+ torch.sum(self.V*self.V)/self.V.shape[0])
      
      total_loss = error_train + regularization_loss + gravity_loss

      optimizer.zero_grad()
      total_loss.backward()
      optimizer.step()
      if (i % 10 == 0) or i == num_iterations:
        losses = {
      'train_error_observed': error_train,
      'test_error_observed': error_test,
  }
        loss_components = {
      'observed_loss': error_train,
      'regularization_loss': regularization_loss,
      'gravity_loss': gravity_loss,
        }
        print(f'\r iteration {i}:train_error = {total_loss} ; test_error = {error_test};loss_components:{loss_components}',end='')
    

In [45]:
reg_model = Regularized_CFModel(init_stddev =0.05,regularization_coeff=0.1, gravity_coeff=1.,embedding_dim=50)
reg_model.train(3000,20.,ratings)

 iteration 3000:train_error = 3.404170046573002 ; test_error = 3.962963039965429;loss_components:{'observed_loss': tensor(1.0594, dtype=torch.float64, grad_fn=<MeanBackward0>), 'regularization_loss': tensor(1.0600, grad_fn=<MulBackward0>), 'gravity_loss': tensor(1.2848, grad_fn=<MulBackward0>)})}

Observe that adding the regularization terms results in a higher MSE, both on the training and test set. However, as we will see, the quality of the recommendations improves. This highlights a tension between fitting the observed data and minimizing the regularization terms. Fitting the observed data often emphasizes learning high similarity (between items with many interactions), but a good embedding representation also requires learning low similarity (between items with few or no interactions).

### Inspect the Results on the regularization

In [46]:
movie_neighbors(reg_model, "Aladdin", DOT)
movie_neighbors(reg_model, "Aladdin", COSINE)

Nearest neighbors of : Aladdin (1992).
[Found more than one matching movie. Other candidates: Aladdin and the King of Thieves (1996)]


dot score                            titles  \
94    7.999346                    Aladdin (1992)   
203   6.303487         Back to the Future (1985)   
49    6.199734                  Star Wars (1977)   
233   6.105632                       Jaws (1975)   
264   6.072690  Hunt for Red October, The (1990)   
173   6.009943    Raiders of the Lost Ark (1981)   

                                  genres  
94     Animation-Children-Comedy-Musical  
203                        Comedy-Sci-Fi  
49   Action-Adventure-Romance-Sci-Fi-War  
233                        Action-Horror  
264                      Action-Thriller  
173                     Action-Adventure

Nearest neighbors of : Aladdin (1992).
[Found more than one matching movie. Other candidates: Aladdin and the King of Thieves (1996)]


cosine score                      titles  \
94       1.000000              Aladdin (1992)   
70       0.660801       Lion King, The (1994)   
96       0.659102   Dances with Wolves (1990)   
142      0.651311  Sound of Music, The (1965)   
203      0.651276   Back to the Future (1985)   
185      0.642183  Blues Brothers, The (1980)   

                                genres  
94   Animation-Children-Comedy-Musical  
70          Animation-Children-Musical  
96             Adventure-Drama-Western  
142                            Musical  
203                      Comedy-Sci-Fi  
185              Action-Comedy-Musical

In [47]:
movie_embedding_norm([model, model_lowinit, reg_model])

alt.HConcatChart(...)

Visualize the embeddings

In [417]:
# Visualize the embeddings
tsne_movie_embeddings(reg_model)


Running t-SNE...
[t-SNE] Computing 121 nearest neighbors...
[t-SNE] Indexed 1682 samples in 0.001s...
[t-SNE] Computed neighbors for 1682 samples in 0.060s...
[t-SNE] Computed conditional probabilities for sample 1000 / 1682
[t-SNE] Computed conditional probabilities for sample 1682 / 1682
[t-SNE] Mean sigma: 0.240381
[t-SNE] KL divergence after 250 iterations with early exaggeration: 58.768078
[t-SNE] KL divergence after 400 iterations: 1.657373


alt.HConcatChart(...)

### Conclusion
This concludes this section on matrix factorization models. Note that while the scale of the problem is small enough to allow efficient training using SGD, many practical problems need to be trained using more specialized algorithms such as Alternating Least Squares

To be Implemented - DNN with Softmax 